# Variography

In [ ]:
import geolime as geo

In [ ]:
dh_tom = geo.read_file("../data/dh_tom_comp.geo")

Once the capping value determined, we can create a new property to capp the value above 25.

In [ ]:
dh_tom.set_property(name='Zn_cap', data='Zn_pct')
dh_tom.update_property(name='Zn_cap', data='25', region="(Zn_cap > 25)")

## Normal Score

For simplicity in variography analysis, let's compute the normal scores of the data.


`gauss_score` function returns a numpy array, so let's create a new property on the Drillholes.

In [ ]:
geo.gauss_score(dh_tom['Zn_cap'])

In [ ]:
dh_tom.set_property(name="Zn_gauss", data=geo.gauss_score(dh_tom['Zn_cap']))

## Experimental Analysis

### Lag Creation

For Variography analysis, lag creation can be perfom 
- implicitly with a number of lags and a length of lag
- explicitly with interval values provided.

In [ ]:
lags, tol = geo.generate_lags_from_interval([[0, 10], [10, 20], [20, 40]])

In [ ]:
lags, tol = geo.generate_lags(lag=40, plag=50, nlags=15)

In [ ]:
lags

In [ ]:
tol

Variography Analysis is perform in 2 step:
- finding the main direction 
- computing the semi variogram 1D in the major/semi-major/minor directions

The finding of the main direction is perform through the analysis of variomap is the different planes.
- Analysis around the Z axis for the azimuth using `vario_map` / `vario_contour`;
- Once found the main azimuth, analysis around the X axis for the dip using `vario_contour_dip`;
- Once found the correspond azimuth and dip, analysis around the Z axis for the pitch using `vario_contour_pitch`

### Finding main direction

In [ ]:
geo.vario_map(
    geo_object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    lags=lags,
    tol=tol,
    n_az=15,
    atol=15,
    backend=geo.GeostatsBackend.RUST,
    rust_multithread=True
)

In [ ]:
geo.vario_contour(
    geo_object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    lags=lags,
    tol=tol,
    n_az=15,
    atol=10,
    user_azimuth=145,
    backend=geo.GeostatsBackend.RUST,
    rust_multithread=True
)

In [ ]:
geo.vario_contour_dip(
    geo_object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    lags=lags,
    tol=tol,
    azimuth=145,
    n_dip=18,
    atol=10,
    user_dip=30,
    c_step=None,
    save_file=None,
    backend=geo.GeostatsBackend.RUST,
    rust_multithread=True
)

In [ ]:
lags, tol = geo.generate_lags(lag=5, plag=50, nlags=15)

In [ ]:
geo.vario_contour_pitch(
    geo_object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    lags=lags,
    tol=tol,
    azimuth=145,
    dip=30,
    n_pitch=15,
    atol=10,
    user_pitch=40,
    c_step=None,
    save_file=None,
    backend=geo.GeostatsBackend.RUST,
    rust_multithread=True
)

### Computing Major/Semi-major/minor 1D variograms

In [ ]:
lags, tol = geo.generate_lags(lag=40, plag=50, nlags=15)

In [ ]:
vario_exp_major = geo.variogram(
    object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    geographic_azimuth=145,
    dip=30,
    pitch=40,
    lags=lags,
    tol=tol,
    atol=15
)

In [ ]:
vario_exp_major

In [ ]:
geo.plot_semivariogram(
    variograms=[vario_exp_major],
    display_npairs=True
)

In [ ]:
vario_exp_semi_major = geo.variogram(
    object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    geographic_azimuth=145,
    dip=30,
    pitch=-50,
    lags=lags,
    tol=tol,
    atol=15
)

geo.plot_semivariogram(
    variograms=[vario_exp_semi_major],
    display_npairs=True
)

In [ ]:
lags, tol = geo.generate_lags(lag=2, plag=50, nlags=15)

In [ ]:
vario_exp_minor = geo.variogram(
    object=dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    geographic_azimuth=145,
    dip=-60,
    pitch=40,
    lags=lags,
    tol=tol,
    atol=30
)

geo.plot_semivariogram(
    variograms=[vario_exp_minor],
    display_npairs=True
)

### Computing Downhole Variogram

In [ ]:
lags, tol = geo.generate_lags(lag=1., plag=50, nlags=20)

In [ ]:
vario_exp_bh = geo.variogram_downhole(
    object= dh_tom,
    attribute="Zn_gauss",
    region="Zn_gauss.notna()",
    lags=lags,
    tol=tol,
)

In [ ]:
geo.plot_semivariogram(
    variograms=[vario_exp_bh],
    display_npairs=True
)

## Automatic Fitting

Automatic Fitting uses an empty model to fit along experimental variograms. Fitting is usually performed in 2 steps : first fit the nugget and then fit the other structures.

### Fitting the Nugget

In [ ]:
nugget_model = geo.Nugget() + geo.Spherical()

The fitting algorithm can be set up to preferrentially fit the small ranges using the INVERSE_DISTANCE or SQUARED_INVERSE_DISTANCE.

In [ ]:
geo.model_fit(
    variograms=[vario_exp_bh],
    cov=nugget_model,
    weighting_method=geo.VarioFitWeightingMethod.SQUARED_INVERSE_DISTANCE
)

In [ ]:
print(nugget_model)

Model and experimental variogram can be plotted on the same graphic by specifying the parameter `model` and `model_angles`. Note that for downhole varigram the model_angles values do not have any importance.

In [ ]:
geo.plot_semivariogram(
    variograms=[vario_exp_bh],
    model=nugget_model,
    model_angles=[{"azi":0, "dip":90, "pitch":90}],
    display_npairs=True
)

Each structure component can be accessed using the `cov_elem_list` attribute.

In [ ]:
nugget_model.cov_elem_list[0].sill

### Fitting the structures

In [ ]:
model =  geo.Nugget() + geo.Spherical() + geo.Spherical()

In [ ]:
short_range_spherical_ratio = 0.6
long_range_spherical_ratio = 0.4

In [ ]:
geo.model_fit(
    variograms=[
        vario_exp_major,
        vario_exp_semi_major,
        vario_exp_minor
    ],
    cov=model,
    constraints=[
        {"sill_fixed":0.13},
        {
            "sill_max": short_range_spherical_ratio * (vario_exp_major.attrs["variable_var"] - 0.13),
            "angle_fixed_0": 145,
            "angle_fixed_1": 60,
            "angle_fixed_2": 40,
            "scale_max_0":100,
            "scale_max_1":100,
            "scale_max_2":20 
        },
        {
            "sill_max": long_range_spherical_ratio * (vario_exp_major.attrs["variable_var"] - 0.13),
            "angle_fixed_0": 145,
            "angle_fixed_1": 60,
            "angle_fixed_2": 40, 
        }
    ]
)

In [ ]:
geo.plot_semivariogram(
    variograms=[vario_exp_major, vario_exp_semi_major, vario_exp_minor],
    model=model,
    model_angles=[
        {"azi":145, "dip":60, "pitch":40},
        {"azi":145, "dip":60, "pitch":-50},
        {"azi":145, "dip":-30, "pitch":40},
    ],
    display_npairs=True
)

In [ ]:
print(model)

In [ ]:
dh_tom.to_file("../data/dh_tom_comp_capped.geo")